In [439]:
import warnings
warnings.filterwarnings('ignore')
import pickle
import numpy as np
import pandas as pd
import json
from textblob import TextBlob
import nltk
from scipy import spatial
import torch
import spacy
en_nlp = spacy.load('en')

In [440]:
train = pd.read_json("C:/Users/KIIT/Downloads/stanford-question-answering-dataset/train-v1.1.json")

In [441]:
valid = pd.read_json("C:/Users/KIIT/Downloads/stanford-question-answering-dataset/dev-v1.1.json")

In [443]:
train

data  version
0    {'title': 'University_of_Notre_Dame', 'paragra...      1.1
1    {'title': 'Beyoncé', 'paragraphs': [{'context'...      1.1
2    {'title': 'Montana', 'paragraphs': [{'context'...      1.1
3    {'title': 'Genocide', 'paragraphs': [{'context...      1.1
4    {'title': 'Antibiotics', 'paragraphs': [{'cont...      1.1
..                                                 ...      ...
437  {'title': 'Police', 'paragraphs': [{'context':...      1.1
438  {'title': 'Punjab,_Pakistan', 'paragraphs': [{...      1.1
439  {'title': 'Infection', 'paragraphs': [{'contex...      1.1
440  {'title': 'Hunting', 'paragraphs': [{'context'...      1.1
441  {'title': 'Kathmandu', 'paragraphs': [{'contex...      1.1

[442 rows x 2 columns]

In [8]:
context = []
ques = []
answer_st = []
answer_text = []
for i in range(train.shape[0]):
    topic = train.iloc[i,0]['paragraphs']
    for sub_para in topic:
        for q_a in sub_para['qas']:
            ques.append(q_a['question'])
            answer_st.append(q_a['answers'][0]['answer_start'])
            answer_text.append(q_a['answers'][0]['text'])
            context.append(sub_para['context'])   
data = pd.DataFrame({"context":context, "question": ques, "answer_start": answer_st, "text": answer_text})

In [9]:
data.head()

context  \
0  Architecturally, the school has a Catholic cha...   
1  Architecturally, the school has a Catholic cha...   
2  Architecturally, the school has a Catholic cha...   
3  Architecturally, the school has a Catholic cha...   
4  Architecturally, the school has a Catholic cha...   

                                            question  answer_start  \
0  To whom did the Virgin Mary allegedly appear i...           515   
1  What is in front of the Notre Dame Main Building?           188   
2  The Basilica of the Sacred heart at Notre Dame...           279   
3                  What is the Grotto at Notre Dame?           381   
4  What sits on top of the Main Building at Notre...            92   

                                      text  
0               Saint Bernadette Soubirous  
1                a copper statue of Christ  
2                        the Main Building  
3  a Marian place of prayer and reflection  
4       a golden statue of the Virgin Mary

In [17]:
paras = list(data["context"].drop_duplicates().reset_index(drop= True))
blob = TextBlob(" ".join(paras))
sentences = [item.raw for item in blob.sentences]


In [18]:
type(sentences)

list

In [19]:
from model import InferSent
MODEL_PATH = 'C:/Users/KIIT/Downloads/infersent1.pkl'
params_model = {'bsize': 64, 'word_emb_dim': 300, 'enc_lstm_dim': 2048,
'pool_type': 'max', 'dpout_model': 0.0, 'version': 1}
model = InferSent(params_model)
model.load_state_dict(torch.load(MODEL_PATH))

<All keys matched successfully>

In [20]:
model

InferSent(
  (enc_lstm): LSTM(300, 2048, bidirectional=True)
)

In [21]:
W2V_PATH = 'glove.6B.300d.txt'
model.set_w2v_path(W2V_PATH)

In [22]:
model.build_vocab(sentences, tokenize=True)

Found 23836(/44941) words with w2v vectors
Vocab size : 23836


In [23]:
questions = list(data["question"])

In [24]:
len(questions)

24821

In [26]:
dict_embeddings={}
for i in range(len(questions)):
    print(i)
    dict_embeddings[questions[i]] = model.encode([questions[i]], tokenize=True)
    print(dict_embeddings[questions[i]])

0
[[ 0.10155731  0.13133855  0.04750498 ...  0.00519656 -0.01592858
   0.02751505]]
1
[[ 0.09717871  0.08103351 -0.00149178 ...  0.00454458 -0.01592858
  -0.02113115]]
2
[[ 0.10515574  0.07426725  0.02433623 ...  0.01846062 -0.01592858
   0.00319012]]
3
[[ 0.04641258  0.11146306 -0.04809947 ... -0.00565137 -0.00701654
  -0.0024975 ]]
4
[[ 0.10152459  0.10376334  0.08552857 ...  0.0030086  -0.00701654
  -0.00249751]]
5
[[ 0.06358585  0.05922984  0.03428819 ...  0.01514885 -0.01592858
  -0.00638389]]
6
[[ 0.05183944  0.01507794  0.03144719 ... -0.00947422 -0.00525761
   0.01281748]]
7
[[ 0.04641258  0.14540213 -0.01488692 ...  0.05263807 -0.01592857
  -0.00340718]]
8
[[ 0.07186487  0.03961874 -0.0523049  ...  0.03222778 -0.00701654
   0.02762142]]
9
[[ 0.03504578  0.10311811  0.03363656 ...  0.04771533 -0.00701654
   0.03944355]]
10
[[ 0.04641258  0.02457436 -0.03249124 ... -0.0084547  -0.01592857
  -0.0230539 ]]
11
[[ 0.06712652  0.02976536  0.09650671 ...  0.00114727 -0.01592858
   0.0

[[ 0.03413428  0.0727597   0.04762327 ... -0.00053891 -0.00234457
   0.07803166]]
98
[[ 0.14422719  0.05383622  0.03845226 ... -0.02786369 -0.01592857
   0.02269249]]
99
[[ 0.07239058  0.09076311  0.12832095 ... -0.02738648 -0.01592858
  -0.00793163]]
100
[[ 0.11528769  0.03998306  0.10515639 ... -0.00845471 -0.01592858
  -0.0132298 ]]
101
[[ 0.0751541   0.04141131  0.02776756 ... -0.00565137 -0.00701654
  -0.00249751]]
102
[[ 0.12873681  0.05230824  0.15066035 ... -0.00565136 -0.00701655
   0.02905651]]
103
[[ 0.08208334  0.05183748  0.03868226 ...  0.01779602 -0.01592858
   0.02202359]]
104
[[ 0.07185365  0.07373466  0.04565821 ... -0.00356991 -0.01592858
   0.03426597]]
105
[[ 0.12885977  0.0517684   0.07799572 ...  0.00581362 -0.01592857
   0.03072853]]
106
[[ 0.06405945  0.09766341  0.01544569 ...  0.00035919 -0.01592857
   0.08096953]]
107
[[ 0.04612393 -0.01586417  0.00576449 ...  0.02807408 -0.01592857
  -0.0006883 ]]
108
[[ 0.12408294  0.08129232  0.02195284 ... -0.02786369 -0

[[ 0.06792359 -0.01585471  0.04207536 ... -0.01061942 -0.01592858
   0.11133314]]
195
[[ 0.06425735  0.05154742  0.045887   ... -0.0024841  -0.01592858
   0.04547086]]
196
[[ 0.07480681  0.03019126 -0.00219876 ...  0.01461836 -0.01592857
   0.09996317]]
197
[[ 0.01640774  0.12247203  0.02486247 ... -0.02786369 -0.01592857
  -0.01039504]]
198
[[ 0.08138511  0.09634688  0.0101623  ... -0.00565136 -0.00701655
   0.04477634]]
199
[[ 0.07140168  0.09434099 -0.01932271 ... -0.0278637   0.01503588
   0.04586703]]
200
[[ 0.07013501  0.03998306  0.06709372 ... -0.0278637  -0.01592858
   0.03956774]]
201
[[ 0.05570954  0.04873629 -0.02630326 ... -0.0278637  -0.01592858
   0.050274  ]]
202
[[ 0.07425489 -0.0120601   0.00515789 ...  0.05191758 -0.01592858
  -0.02040284]]
203
[[ 0.07035262  0.10074365  0.03067459 ... -0.01993482 -0.01592858
   0.02509486]]
204
[[ 0.07221959  0.04920553  0.037445   ... -0.01501005 -0.01592858
   0.03956774]]
205
[[ 0.03504578  0.06405235  0.03770984 ... -0.00565137 

[[ 0.02511704  0.0494245   0.0012588  ... -0.0278637  -0.01592858
   0.01088023]]
291
[[ 0.08080279  0.04124589  0.06959896 ... -0.00705895 -0.01592858
   0.03303739]]
292
[[ 0.06342783 -0.01676856  0.15809606 ...  0.02649217 -0.01592857
   0.01719498]]
293
[[ 0.10726847  0.09138703  0.14879337 ...  0.00444364 -0.01592857
  -0.02223085]]
294
[[ 0.07095974  0.11387371  0.09536952 ...  0.08854649 -0.01592858
  -0.01286607]]
295
[[ 0.07645756 -0.01989697  0.04019569 ... -0.0278637  -0.01592858
   0.02124705]]
296
[[ 0.05977099  0.01512715  0.0444389  ...  0.02400985 -0.01285123
   0.09081741]]
297
[[ 0.09087119  0.01638024  0.16223703 ...  0.04022055 -0.01592858
   0.0305048 ]]
298
[[ 0.09881891  0.06259341  0.0869874  ...  0.00578218 -0.01592858
   0.02334332]]
299
[[ 0.05443211  0.04417852 -0.04809947 ... -0.0278637  -0.01592858
   0.03877931]]
300
[[ 0.05183965  0.04199762  0.04050545 ... -0.00503377  0.0043781
  -0.0230539 ]]
301
[[ 0.08418612  0.04678817 -0.00855806 ...  0.01198157 -

[[ 0.09275026  0.06371234  0.02588327 ... -0.0278637  -0.01592858
   0.00657936]]
387
[[ 0.09297004  0.07543885  0.10435995 ... -0.00699326 -0.01592858
   0.03212766]]
388
[[ 0.12123792  0.04874447  0.12964445 ...  0.01609464 -0.01592858
   0.00635596]]
389
[[ 0.08453706  0.07919979  0.03140533 ...  0.00707434 -0.01592858
   0.02714664]]
390
[[ 0.08585723  0.02722911 -0.01441396 ... -0.0278637  -0.01592858
   0.02442663]]
391
[[ 0.10797779  0.04521506  0.02144411 ... -0.01589853 -0.01592858
  -0.004022  ]]
392
[[ 0.09441882  0.01162988  0.10920321 ...  0.00978943 -0.00186903
   0.08387313]]
393
[[ 0.07465821  0.0055256  -0.01873311 ... -0.02231583 -0.01592858
   0.01487162]]
394
[[ 0.11909356  0.07871855  0.07818686 ... -0.00147547 -0.01592857
   0.04000242]]
395
[[ 0.11534598  0.08293173  0.05586994 ...  0.00417279 -0.01592857
   0.01421804]]
396
[[ 0.08498358  0.04672205  0.12418643 ...  0.01308904 -0.01592858
   0.00186104]]
397
[[ 0.11585054  0.0526852   0.03965485 ...  0.00465664 

...

[[ 0.10101846  0.0944167   0.02331216 ...  0.02551418 -0.01592858
  -0.02305389]]
24427
[[ 0.08056507  0.07471218  0.05900278 ...  0.02551419 -0.01592858
  -0.0009278 ]]
24428
[[ 0.07846699  0.14751975  0.03367088 ...  0.00250396 -0.01592857
  -0.0230539 ]]
24429
[[ 0.07606557  0.11220293  0.05325096 ...  0.01228102 -0.01592857
   0.01423847]]
24430
[[ 0.08205781  0.14314577  0.02008961 ...  0.06819453 -0.01592858
   0.03730803]]
24431
[[ 0.07980988  0.0487217   0.00389263 ...  0.09893062 -0.01592858
   0.02199252]]
24432
[[ 0.09928682  0.0256715  -0.02987646 ...  0.01633487 -0.01592857
   0.02886273]]
24433
[[ 0.16149169  0.10967182  0.07431895 ... -0.00047674 -0.01592858
   0.02466765]]
24434
[[ 0.12260894  0.11065359 -0.01508101 ...  0.0223065  -0.01592857
   0.02930585]]
24435
[[ 0.11160168  0.09254228  0.08145416 ... -0.00259533 -0.01592858
   0.00454699]]
24436
[[ 0.12668286  0.11553331  0.04354097 ...  0.02762985 -0.01592858
   0.04853311]]
24437
[[ 0.09722152  0.0724328   0.067

[[ 0.03504578  0.03998306  0.01507691 ... -0.0278637  -0.01592858
  -0.0230539 ]]
24522
[[ 0.03554321  0.03558781  0.01492879 ... -0.01993483 -0.01592858
  -0.00434846]]
24523
[[ 0.07503493  0.030705    0.02106086 ... -0.02736082  0.02238618
  -0.00281228]]
24524
[[ 0.04596198  0.04963159  0.02209317 ... -0.01993482 -0.01592858
  -0.00434844]]
24525
[[ 0.05309457  0.09378304 -0.01135956 ... -0.01716488 -0.01592857
   0.02137463]]
24526
[[ 0.05105041  0.01649086 -0.00884785 ... -0.00744931 -0.01592858
   0.0137254 ]]
24527
[[ 0.03136166  0.02546435 -0.03213534 ... -0.02177834 -0.01472494
   0.02543631]]
24528
[[ 0.08944505  0.08054411  0.02421989 ... -0.01716488 -0.01592858
   0.01390026]]
24529
[[ 0.08944505  0.08054411  0.02421989 ... -0.01716488 -0.01592858
   0.01390026]]
24530
[[ 0.07518744  0.04688525  0.04466447 ... -0.02786369 -0.01592857
   0.00324655]]
24531
[[ 0.06086725  0.05636038  0.01611773 ... -0.0227219  -0.01592858
   0.01435417]]
24532
[[ 0.04641258 -0.01713103  0.034

   0.04311845]]
24615
[[ 0.05157736  0.03913826  0.03559526 ... -0.01993483 -0.01592857
  -0.00907605]]
24616
[[ 0.08427358  0.06388356  0.03360927 ... -0.01202297 -0.01592857
   0.01899232]]
24617
[[ 0.06064139 -0.02249637  0.01676388 ... -0.0278637  -0.01592858
   0.01484743]]
24618
[[ 0.05258772  0.04953745  0.05421198 ...  0.03665611 -0.01592858
  -0.02305389]]
24619
[[ 0.06073308 -0.01425371  0.02391431 ... -0.01993483 -0.01592857
  -0.0230539 ]]
24620
[[ 0.11312693  0.05141965  0.05357835 ... -0.02786369 -0.01592857
   0.05336019]]
24621
[[ 0.04453022  0.01801925  0.03252321 ... -0.02012665  0.01785294
   0.00864705]]
24622
[[ 0.04429562  0.00466149 -0.01456015 ... -0.00957549  0.01785295
  -0.0161365 ]]
24623
[[ 0.12038962  0.07214171  0.12920158 ...  0.04084116 -0.01592857
   0.05322213]]
24624
[[0.1028051  0.09930712 0.00873199 ... 0.042281   0.02161659 0.04582186]]
24625
[[ 0.06078519 -0.00769257 -0.01417113 ... -0.01723078 -0.01592857
   0.00357344]]
24626
[[ 0.08678835  0.0

[[ 0.09564414  0.10021859  0.0498096  ...  0.00061778 -0.01592858
   0.05364011]]
24710
[[ 0.09218517  0.11272831  0.01593714 ...  0.03442255 -0.01592857
   0.04674742]]
24711
[[ 0.06225888  0.11632049  0.0138627  ...  0.0008414  -0.01592858
   0.09061668]]
24712
[[ 0.08561262  0.08453055  0.10494357 ... -0.00703904 -0.01592858
   0.02384319]]
24713
[[ 0.10650559  0.10616042 -0.02457523 ...  0.0499624  -0.01592858
   0.03186383]]
24714
[[ 0.05604501  0.01966515  0.03932327 ... -0.0278637  -0.01592858
  -0.00672717]]
24715
[[ 0.08189722  0.0614954  -0.09205686 ... -0.00278263 -0.01192422
   0.02601378]]
24716
[[ 0.0182363  -0.06730774 -0.01732444 ... -0.0278637   0.00375776
   0.03339885]]
24717
[[ 0.04184646 -0.01392139  0.00817208 ... -0.00845471 -0.01592858
  -0.00594526]]
24718
[[ 0.10930634  0.11094703 -0.08734879 ...  0.04996238 -0.01325768
   0.1376553 ]]
24719
[[ 0.07253469  0.05703869  0.0659259  ...  0.01835939 -0.01592857
   0.04240535]]
24720
[[ 0.15915886  0.10662991  0.003

[[ 0.06202189  0.06617388  0.11176052 ... -0.0278637   0.02327746
   0.05868998]]
24804
[[ 0.07562286 -0.03908967 -0.00434187 ... -0.0278637  -0.01592858
   0.00184865]]
24805
[[ 0.09238916  0.02524589  0.00989949 ... -0.02786369 -0.01592857
  -0.00163315]]
24806
[[ 0.09238916  0.02524589  0.01617655 ... -0.0278637  -0.01592858
   0.06836086]]
24807
[[ 0.0739568   0.02457436 -0.0391828  ... -0.02786369 -0.00905691
  -0.0230539 ]]
24808
[[ 0.05672874  0.0702491   0.11916112 ... -0.0278637  -0.01592858
   0.01583981]]
24809
[[ 0.03571633  0.02524589 -0.03721718 ... -0.02786369 -0.01592857
   0.01583982]]
24810
[[ 0.03697755  0.02524589 -0.0433221  ... -0.0278637  -0.01592858
   0.01583982]]
24811
[[ 0.10280661  0.10316876  0.11916112 ... -0.0278637  -0.01592858
   0.08409987]]
24812
[[ 0.04641258  0.01268416 -0.0392338  ... -0.00845471 -0.01592858
  -0.0086861 ]]
24813
[[ 0.04300825 -0.00441591  0.03108943 ... -0.00560471  0.00369977
   0.00851272]]
24814
[[ 0.02733097  0.04014262  0.086

In [27]:
len(sentences)

22240

In [28]:
dict_emb={}
for i in range(len(sentences)):
    print(i)
    dict_emb[sentences[i]] = model.encode([sentences[i]], tokenize=True)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700


5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339


6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978


...

15511
15512
15513
15514
15515
15516
15517
15518
15519
15520
15521
15522
15523
15524
15525
15526
15527
15528
15529
15530
15531
15532
15533
15534
15535
15536
15537
15538
15539
15540
15541
15542
15543
15544
15545
15546
15547
15548
15549
15550
15551
15552
15553
15554
15555
15556
15557
15558
15559
15560
15561
15562
15563
15564
15565
15566
15567
15568
15569
15570
15571
15572
15573
15574
15575
15576
15577
15578
15579
15580
15581
15582
15583
15584
15585
15586
15587
15588
15589
15590
15591
15592
15593
15594
15595
15596
15597
15598
15599
15600
15601
15602
15603
15604
15605
15606
15607
15608
15609
15610
15611
15612
15613
15614
15615
15616
15617
15618
15619
15620
15621
15622
15623
15624
15625
15626
15627
15628
15629
15630
15631
15632
15633
15634
15635
15636
15637
15638
15639
15640
15641
15642
15643
15644
15645
15646
15647
15648
15649
15650
15651
15652
15653
15654
15655
15656
15657
15658
15659
15660
15661
15662
15663
15664
15665
15666
15667
15668
15669
15670
15671
15672
15673
15674
15675
15676
1567

16878
16879
16880
16881
16882
16883
16884
16885
16886
16887
16888
16889
16890
16891
16892
16893
16894
16895
16896
16897
16898
16899
16900
16901
16902
16903
16904
16905
16906
16907
16908
16909
16910
16911
16912
16913
16914
16915
16916
16917
16918
16919
16920
16921
16922
16923
16924
16925
16926
16927
16928
16929
16930
16931
16932
16933
16934
16935
16936
16937
16938
16939
16940
16941
16942
16943
16944
16945
16946
16947
16948
16949
16950
16951
16952
16953
16954
16955
16956
16957
16958
16959
16960
16961
16962
16963
16964
16965
16966
16967
16968
16969
16970
16971
16972
16973
16974
16975
16976
16977
16978
16979
16980
16981
16982
16983
16984
16985
16986
16987
16988
16989
16990
16991
16992
16993
16994
16995
16996
16997
16998
16999
17000
17001
17002
17003
17004
17005
17006
17007
17008
17009
17010
17011
17012
17013
17014
17015
17016
17017
17018
17019
17020
17021
17022
17023
17024
17025
17026
17027
17028
17029
17030
17031
17032
17033
17034
17035
17036
17037
17038
17039
17040
17041
17042
17043
1704

18245
18246
18247
18248
18249
18250
18251
18252
18253
18254
18255
18256
18257
18258
18259
18260
18261
18262
18263
18264
18265
18266
18267
18268
18269
18270
18271
18272
18273
18274
18275
18276
18277
18278
18279
18280
18281
18282
18283
18284
18285
18286
18287
18288
18289
18290
18291
18292
18293
18294
18295
18296
18297
18298
18299
18300
18301
18302
18303
18304
18305
18306
18307
18308
18309
18310
18311
18312
18313
18314
18315
18316
18317
18318
18319
18320
18321
18322
18323
18324
18325
18326
18327
18328
18329
18330
18331
18332
18333
18334
18335
18336
18337
18338
18339
18340
18341
18342
18343
18344
18345
18346
18347
18348
18349
18350
18351
18352
18353
18354
18355
18356
18357
18358
18359
18360
18361
18362
18363
18364
18365
18366
18367
18368
18369
18370
18371
18372
18373
18374
18375
18376
18377
18378
18379
18380
18381
18382
18383
18384
18385
18386
18387
18388
18389
18390
18391
18392
18393
18394
18395
18396
18397
18398
18399
18400
18401
18402
18403
18404
18405
18406
18407
18408
18409
18410
1841

19611
19612
19613
19614
19615
19616
19617
19618
19619
19620
19621
19622
19623
19624
19625
19626
19627
19628
19629
19630
19631
19632
19633
19634
19635
19636
19637
19638
19639
19640
19641
19642
19643
19644
19645
19646
19647
19648
19649
19650
19651
19652
19653
19654
19655
19656
19657
19658
19659
19660
19661
19662
19663
19664
19665
19666
19667
19668
19669
19670
19671
19672
19673
19674
19675
19676
19677
19678
19679
19680
19681
19682
19683
19684
19685
19686
19687
19688
19689
19690
19691
19692
19693
19694
19695
19696
19697
19698
19699
19700
19701
19702
19703
19704
19705
19706
19707
19708
19709
19710
19711
19712
19713
19714
19715
19716
19717
19718
19719
19720
19721
19722
19723
19724
19725
19726
19727
19728
19729
19730
19731
19732
19733
19734
19735
19736
19737
19738
19739
19740
19741
19742
19743
19744
19745
19746
19747
19748
19749
19750
19751
19752
19753
19754
19755
19756
19757
19758
19759
19760
19761
19762
19763
19764
19765
19766
19767
19768
19769
19770
19771
19772
19773
19774
19775
19776
1977

20977
20978
20979
20980
20981
20982
20983
20984
20985
20986
20987
20988
20989
20990
20991
20992
20993
20994
20995
20996
20997
20998
20999
21000
21001
21002
21003
21004
21005
21006
21007
21008
21009
21010
21011
21012
21013
21014
21015
21016
21017
21018
21019
21020
21021
21022
21023
21024
21025
21026
21027
21028
21029
21030
21031
21032
21033
21034
21035
21036
21037
21038
21039
21040
21041
21042
21043
21044
21045
21046
21047
21048
21049
21050
21051
21052
21053
21054
21055
21056
21057
21058
21059
21060
21061
21062
21063
21064
21065
21066
21067
21068
21069
21070
21071
21072
21073
21074
21075
21076
21077
21078
21079
21080
21081
21082
21083
21084
21085
21086
21087
21088
21089
21090
21091
21092
21093
21094
21095
21096
21097
21098
21099
21100
21101
21102
21103
21104
21105
21106
21107
21108
21109
21110
21111
21112
21113
21114
21115
21116
21117
21118
21119
21120
21121
21122
21123
21124
21125
21126
21127
21128
21129
21130
21131
21132
21133
21134
21135
21136
21137
21138
21139
21140
21141
21142
2114

In [111]:
dict_emb[sentences[5]]

array([[ 0.08522367,  0.09164818,  0.02191166, ...,  0.00410508,
        -0.04465294,  0.06349701]], dtype=float32)

In [90]:
dict_embeddings[questions[0]]

array([[ 0.10155731,  0.13133855,  0.04750498, ...,  0.00519656,
        -0.01592858,  0.02751505]], dtype=float32)

In [29]:
def get_target(x):
    idx = -1
    for i in range(len(x["sentences"])):
        if x["text"] in x["sentences"][i]: idx = i
    return idx

In [30]:
def process_data(data):
    
    print("step 1")
    data['sentences'] = data['context'].apply(lambda x: [item.raw for item in TextBlob(x).sentences])
    
    print("step 2")
    data["target"] = data.apply(get_target, axis = 1)
    
    print("step 3")
    data['sent_emb'] = data['sentences'].apply(lambda x: [dict_emb[item][0] if item in\
                                                           dict_emb else np.zeros(4096) for item in x])

    print("step 4")
    data['quest_emb'] = data['question'].apply(lambda x: dict_embeddings[x] if x in dict_embeddings else np.zeros(4096) )
        
    return data

In [31]:
data = process_data(data)

step 1
step 2
step 3
step 4


In [120]:
len(data.loc[1,'sentences'])

7

In [121]:
data.loc[1,'quest_emb']

array([[ 0.09717871,  0.08103351, -0.00149178, ...,  0.00454458,
        -0.01592858, -0.02113115]], dtype=float32)

In [32]:
data

context  \
0      Architecturally, the school has a Catholic cha...   
1      Architecturally, the school has a Catholic cha...   
2      Architecturally, the school has a Catholic cha...   
3      Architecturally, the school has a Catholic cha...   
4      Architecturally, the school has a Catholic cha...   
...                                                  ...   
24816  During the Minor Occultation (Ghaybat al-Sughr...   
24817  During the Minor Occultation (Ghaybat al-Sughr...   
24818  The Ismailis differ from Twelvers because they...   
24819  The Ismailis differ from Twelvers because they...   
24820  The Ismailis differ from Twelvers because they...   

                                                question  answer_start  \
0      To whom did the Virgin Mary allegedly appear i...           515   
1      What is in front of the Notre Dame Main Building?           188   
2      The Basilica of the Sacred heart at Notre Dame...           279   
3                      What is the Grotto at Notre Dame?           381   
4      What sits on top of the Main Building at Notre...            92   
...                                                  ...           ...   
24816   What would the deputy endorse the concerns with?           413   
24817  What did the deputies collect in the Imam's be...           499   
24818              How do Ismailis differ from Twelvers?            51   
24819        Who is the elder brother of Musa al-Kadhim?           143   
24820            Who is the father of Isma'il ibn Jafar?           233   

                                          text  \
0                   Saint Bernadette Soubirous   
1                    a copper statue of Christ   
2                            the Main Building   
3      a Marian place of prayer and reflection   
4           a golden statue of the Virgin Mary   
...                                        ...   
24816                       seal and signature   
24817                          zakat and khums   
24818                             living imams   
24819                        Isma'il ibn Jafar   
24820                          Ja'far al-Sadiq   

                                               sentences  target  \
0      [Architecturally, the school has a Catholic ch...       5   
1      [Architecturally, the school has a Catholic ch...       2   
2      [Architecturally, the school has a Catholic ch...       3   
3      [Architecturally, the school has a Catholic ch...       4   
4      [Architecturally, the school has a Catholic ch...       1   
...                                                  ...     ...   
24816  [During the Minor Occultation (Ghaybat al-Sugh...       4   
24817  [During the Minor Occultation (Ghaybat al-Sugh...       5   
24818  [The Ismailis differ from Twelvers because the...       0   
24819  [The Ismailis differ from Twelvers because the...       1   
24820  [The Ismailis differ from Twelvers because the...       1   

                                                sent_emb  \
0      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
1      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
2      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
3      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
4      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
...                                                  ...   
24816  [[0.091791965, 0.013778735, 0.11585791, 0.0269...   
24817  [[0.091791965, 0.013778735, 0.11585791, 0.0269...   
24818  [[0.09960401, 0.07075704, 0.029079493, 0.03823...   
24819  [[0.09960401, 0.07075704, 0.029079493, 0.03823...   
24820  [[0.09960401, 0.07075704, 0.029079493, 0.03823...   

                                               quest_emb  
0      [[0.101557314, 0.13133855, 0.04750498, 0.09257...  
1      [[0.097178705, 0.081033505, -0.0014917753, 0.0...  
2      [[0.105155736, 0.07426725, 0.024336234, 0.1249...  
3      [[0.04641258, 0.111463055, -0.048099466, 0.077...  
4    

In [163]:
# The next few blocks are to explore the way the system matches the question with the part of the context to be 
#  referred using the root word . The root word of question is searched in the passage which many a times leads to the 
# sentence having the correct answer . We won't be using this as a feature at the moment for our model using RNNs .

In [130]:
from nltk import Tree

In [125]:
def to_word_tree(x):
    if x.n_lefts + x.n_rights > 0:
        return Tree(x.orth_, [to_word_tree(child) for child in x.children])
    else:
        return x.orth_

In [161]:
[to_word_tree(sent.root).pretty_print()  for sent in en_nlp(data.loc[2,'question']).sents]

         is                                
  _______|____________________________      
 |          Basilica                  |    
 |    _________|_______               |     
 |   |                 of             |    
 |   |                 |              |     
 |   |               heart          beside 
 |   |    _____________|______        |     
 |   |   |             |      at      to   
 |   |   |             |      |       |     
 |   |   |             |     Dame structure
 |   |   |             |      |       |     
 ?  The the          Sacred Notre   which  



[None]

In [132]:
data.loc[5,'question']

'When did the Scholastic Magazine of Notre dame begin publishing?'

In [133]:
for i in data.loc[1,'sentences']:
    [to_word_tree(sent.root).pretty_print()  for sent in en_nlp(i).sents]

                    has                              
        _____________|_________________               
       |         |   |  school     character         
       |         |   |    |      ______|________      
Architecturally  ,   .   the    a            Catholic

                          is                                  
  ________________________|_______________                     
 |    |            |                    statue                
 |    |            |                  ____|_________           
 |    |           dome               |    |         of        
 |    |    ________|______           |    |         |          
 |    |   |            Building      |    |        Mary       
 |    |   |     __________|______    |    |      ___|_____     
Atop  .  gold the        Main    's  a  golden the      Virgin

                                                is                                                  
  ______________________________________________|_____

In [59]:
data.loc[0,'sentences']

['Architecturally, the school has a Catholic character.',
 "Atop the Main Building's gold dome is a golden statue of the Virgin Mary.",
 'Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend "Venite Ad Me Omnes".',
 'Next to the Main Building is the Basilica of the Sacred Heart.',
 'Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection.',
 'It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858.',
 'At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.']

In [256]:
for i in data.loc[152,'sentences']:
    [to_word_tree(sent.root).pretty_print()  for sent in en_nlp(i).sents]

                          grown                                                            
  __________________________|____________________________________________                   
 |   |        |        |           Since                                 |                 
 |   |        |        |             |                                   |                  
 |   |        |        |        construction                             |                 
 |   |        |        |     ________|___________                        |                  
 |   |        |        |    |                    of                    plant               
 |   |        |        |    |                    |                _______|_______           
 |   |        |        |    |                buildings           |           university    
 |   |        |        |    |         ___________|_______        |        _______|_______   
 ,  has substantially  .   the      its                oldest physical  the

In [257]:
data.loc[152,'sentences']

["Since the construction of its oldest buildings, the university's physical plant has grown substantially.",
 'Over the years 29 residence halls have been built to accommodate students and each has been constructed with its own chapel.',
 'Many academic building were added together with a system of libraries, the most prominent of which is the Theodore Hesburgh Library, built in 1963 and today containing almost 4 million books.',
 'Since 2004, several buildings have been added, including the DeBartolo Performing Arts Center, the Guglielmino Complex, and the Jordan Hall of Science.',
 'Additionally, a new residence for men, Duncan Hall, was begun on March 8, 2007, and began accepting residents for the Fall 2008 semester.',
 'Ryan Hall was completed and began housing undergraduate women in the fall of 2009.',
 'A new engineering building, Stinson-Remick Hall, a new combination Center for Social Concerns/Institute for Church Life building, Geddes Hall, and a law school addition have recen

In [135]:
from nltk.stem.lancaster import LancasterStemmer
st = LancasterStemmer()

In [33]:
import keras

Using TensorFlow backend.


In [431]:
from keras.models import Sequential, Model
from keras.layers.embeddings import Embedding
from keras.layers import Input, Activation, Dense, Permute, Dropout, Flatten
from keras.layers import SpatialDropout1D
from keras.layers import LSTM,Bidirectional
from keras.utils.data_utils import get_file
from keras.preprocessing.sequence import pad_sequences
from keras import backend as K

In [143]:
data

context  \
0      Architecturally, the school has a Catholic cha...   
1      Architecturally, the school has a Catholic cha...   
2      Architecturally, the school has a Catholic cha...   
3      Architecturally, the school has a Catholic cha...   
4      Architecturally, the school has a Catholic cha...   
...                                                  ...   
24763  During the Minor Occultation (Ghaybat al-Sughr...   
24764  During the Minor Occultation (Ghaybat al-Sughr...   
24765  The Ismailis differ from Twelvers because they...   
24766  The Ismailis differ from Twelvers because they...   
24767  The Ismailis differ from Twelvers because they...   

                                                question  answer_start  \
0      To whom did the Virgin Mary allegedly appear i...           515   
1      What is in front of the Notre Dame Main Building?           188   
2      The Basilica of the Sacred heart at Notre Dame...           279   
3                      What is the Grotto at Notre Dame?           381   
4      What sits on top of the Main Building at Notre...            92   
...                                                  ...           ...   
24763   What would the deputy endorse the concerns with?           413   
24764  What did the deputies collect in the Imam's be...           499   
24765              How do Ismailis differ from Twelvers?            51   
24766        Who is the elder brother of Musa al-Kadhim?           143   
24767            Who is the father of Isma'il ibn Jafar?           233   

                                          text  \
0                   Saint Bernadette Soubirous   
1                    a copper statue of Christ   
2                            the Main Building   
3      a Marian place of prayer and reflection   
4           a golden statue of the Virgin Mary   
...                                        ...   
24763                       seal and signature   
24764                          zakat and khums   
24765                             living imams   
24766                        Isma'il ibn Jafar   
24767                          Ja'far al-Sadiq   

                                               sentences  target  \
0      [Architecturally, the school has a Catholic ch...       5   
1      [Architecturally, the school has a Catholic ch...       2   
2      [Architecturally, the school has a Catholic ch...       3   
3      [Architecturally, the school has a Catholic ch...       4   
4      [Architecturally, the school has a Catholic ch...       1   
...                                                  ...     ...   
24763  [During the Minor Occultation (Ghaybat al-Sugh...       4   
24764  [During the Minor Occultation (Ghaybat al-Sugh...       5   
24765  [The Ismailis differ from Twelvers because the...       0   
24766  [The Ismailis differ from Twelvers because the...       1   
24767  [The Ismailis differ from Twelvers because the...       1   

                                                sent_emb  \
0      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
1      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
2      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
3      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
4      [[0.086897895, 0.026372066, 0.015878633, 0.083...   
...                                                  ...   
24763  [[0.091791965, 0.013778735, 0.11585791, 0.0269...   
24764  [[0.091791965, 0.013778735, 0.11585791, 0.0269...   
24765  [[0.09960401, 0.07075704, 0.029079493, 0.03823...   
24766  [[0.09960401, 0.07075704, 0.029079493, 0.03823...   
24767  [[0.09960401, 0.07075704, 0.029079493, 0.03823...   

                                               quest_emb  
0      [[0.101557314, 0.13133855, 0.04750498, 0.09257...  
1      [[0.097178705, 0.081033505, -0.0014917753, 0.0...  
2      [[0.105155736, 0.07426725, 0.024336234, 0.1249...  
3      [[0.04641258, 0.111463055, -0.048099466, 0.077...  
4    

In [255]:
x = data.loc[0,'sent_emb'][1]
np.linalg.norm(x)

4.958491

In [258]:
x = data.loc[0,'quest_emb'][0]
np.linalg.norm(x)

4.4360323

In [140]:
data = data[data['target'] != -1]
data.reset_index(inplace=True)

In [142]:
data.drop('index',axis=1,inplace=True)

In [319]:
context = pd.DataFrame()
for i in range(24821):
    print(i)
    if len(data.loc[i,'sent_emb']) < 8 :
        
        for j in range(len(data.loc[i,'sent_emb'])):
            context.loc[i, "column_cos_"+"%s"%j] = np.linalg.norm(data.loc[i,'sent_emb'][j])

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083


3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3752
3753
3754
3755
3756
3757
3758


5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341
5342
5343
5344
5345
5346
5347
5348
5349
5350
5351
5352
5353
5354
5355
5356
5357
5358
5359
5360
5361
5362
5363
5364
5365
5366
5367
5368
5369
5370
5371
5372
5373
5374
5375
5376
5377
5378
5379
5380
5381
5382
5383
5384
5385
5386
5387
5388
5389
5390
5391
5392
5393
5394
5395
5396
5397
5398
5399
5400
5401
5402
5403
5404
5405
5406
5407
5408
5409
5410
5411
5412
5413
5414
5415
5416
5417
5418
5419
5420
5421
5422
5423
5424
5425
5426
5427
5428
5429
5430
5431
5432
5433
5434
5435
5436
5437


6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978
6979
6980
6981
6982
6983
6984
6985
6986
6987
6988
6989
6990
6991
6992
6993
6994
6995
6996
6997
6998
6999
7000
7001
7002
7003
7004
7005
7006
7007
7008
7009
7010
7011
7012
7013
7014
7015
7016
7017
7018
7019
7020
7021
7022
7023
7024
7025
7026
7027
7028
7029
7030
7031
7032
7033
7034
7035
7036
7037
7038
7039
7040
7041
7042
7043
7044
7045
7046
7047
7048
7049
7050
7051
7052
7053
7054
7055
7056
7057
7058
7059
7060
7061
7062
7063
7064
7065
7066
7067
7068
7069
7070
7071
7072
7073
7074
7075
7076
7077
7078
7079
7080
7081
7082
7083
7084
7085
7086
7087
7088
7089
7090
7091
7092
7093
7094
7095
7096


...

19925
19926
19927
19928
19929
19930
19931
19932
19933
19934
19935
19936
19937
19938
19939
19940
19941
19942
19943
19944
19945
19946
19947
19948
19949
19950
19951
19952
19953
19954
19955
19956
19957
19958
19959
19960
19961
19962
19963
19964
19965
19966
19967
19968
19969
19970
19971
19972
19973
19974
19975
19976
19977
19978
19979
19980
19981
19982
19983
19984
19985
19986
19987
19988
19989
19990
19991
19992
19993
19994
19995
19996
19997
19998
19999
20000
20001
20002
20003
20004
20005
20006
20007
20008
20009
20010
20011
20012
20013
20014
20015
20016
20017
20018
20019
20020
20021
20022
20023
20024
20025
20026
20027
20028
20029
20030
20031
20032
20033
20034
20035
20036
20037
20038
20039
20040
20041
20042
20043
20044
20045
20046
20047
20048
20049
20050
20051
20052
20053
20054
20055
20056
20057
20058
20059
20060
20061
20062
20063
20064
20065
20066
20067
20068
20069
20070
20071
20072
20073
20074
20075
20076
20077
20078
20079
20080
20081
20082
20083
20084
20085
20086
20087
20088
20089
20090
2009

21302
21303
21304
21305
21306
21307
21308
21309
21310
21311
21312
21313
21314
21315
21316
21317
21318
21319
21320
21321
21322
21323
21324
21325
21326
21327
21328
21329
21330
21331
21332
21333
21334
21335
21336
21337
21338
21339
21340
21341
21342
21343
21344
21345
21346
21347
21348
21349
21350
21351
21352
21353
21354
21355
21356
21357
21358
21359
21360
21361
21362
21363
21364
21365
21366
21367
21368
21369
21370
21371
21372
21373
21374
21375
21376
21377
21378
21379
21380
21381
21382
21383
21384
21385
21386
21387
21388
21389
21390
21391
21392
21393
21394
21395
21396
21397
21398
21399
21400
21401
21402
21403
21404
21405
21406
21407
21408
21409
21410
21411
21412
21413
21414
21415
21416
21417
21418
21419
21420
21421
21422
21423
21424
21425
21426
21427
21428
21429
21430
21431
21432
21433
21434
21435
21436
21437
21438
21439
21440
21441
21442
21443
21444
21445
21446
21447
21448
21449
21450
21451
21452
21453
21454
21455
21456
21457
21458
21459
21460
21461
21462
21463
21464
21465
21466
21467
2146

22672
22673
22674
22675
22676
22677
22678
22679
22680
22681
22682
22683
22684
22685
22686
22687
22688
22689
22690
22691
22692
22693
22694
22695
22696
22697
22698
22699
22700
22701
22702
22703
22704
22705
22706
22707
22708
22709
22710
22711
22712
22713
22714
22715
22716
22717
22718
22719
22720
22721
22722
22723
22724
22725
22726
22727
22728
22729
22730
22731
22732
22733
22734
22735
22736
22737
22738
22739
22740
22741
22742
22743
22744
22745
22746
22747
22748
22749
22750
22751
22752
22753
22754
22755
22756
22757
22758
22759
22760
22761
22762
22763
22764
22765
22766
22767
22768
22769
22770
22771
22772
22773
22774
22775
22776
22777
22778
22779
22780
22781
22782
22783
22784
22785
22786
22787
22788
22789
22790
22791
22792
22793
22794
22795
22796
22797
22798
22799
22800
22801
22802
22803
22804
22805
22806
22807
22808
22809
22810
22811
22812
22813
22814
22815
22816
22817
22818
22819
22820
22821
22822
22823
22824
22825
22826
22827
22828
22829
22830
22831
22832
22833
22834
22835
22836
22837
2283

24042
24043
24044
24045
24046
24047
24048
24049
24050
24051
24052
24053
24054
24055
24056
24057
24058
24059
24060
24061
24062
24063
24064
24065
24066
24067
24068
24069
24070
24071
24072
24073
24074
24075
24076
24077
24078
24079
24080
24081
24082
24083
24084
24085
24086
24087
24088
24089
24090
24091
24092
24093
24094
24095
24096
24097
24098
24099
24100
24101
24102
24103
24104
24105
24106
24107
24108
24109
24110
24111
24112
24113
24114
24115
24116
24117
24118
24119
24120
24121
24122
24123
24124
24125
24126
24127
24128
24129
24130
24131
24132
24133
24134
24135
24136
24137
24138
24139
24140
24141
24142
24143
24144
24145
24146
24147
24148
24149
24150
24151
24152
24153
24154
24155
24156
24157
24158
24159
24160
24161
24162
24163
24164
24165
24166
24167
24168
24169
24170
24171
24172
24173
24174
24175
24176
24177
24178
24179
24180
24181
24182
24183
24184
24185
24186
24187
24188
24189
24190
24191
24192
24193
24194
24195
24196
24197
24198
24199
24200
24201
24202
24203
24204
24205
24206
24207
2420

KeyError: 24768

In [320]:
context.fillna(0, inplace=True)
context

column_cos_0  column_cos_1  column_cos_2  column_cos_3  column_cos_4  \
0          4.491021      4.958491      5.647708      4.505395      4.748401   
1          4.491021      4.958491      5.647708      4.505395      4.748401   
2          4.491021      4.958491      5.647708      4.505395      4.748401   
3          4.491021      4.958491      5.647708      4.505395      4.748401   
4          4.491021      4.958491      5.647708      4.505395      4.748401   
...             ...           ...           ...           ...           ...   
24763      5.381973      4.617072      4.535333      5.528133      5.333409   
24764      5.381973      4.617072      4.535333      5.528133      5.333409   
24765      5.226763      4.981749      5.798151      5.616116      0.000000   
24766      5.226763      4.981749      5.798151      5.616116      0.000000   
24767      5.226763      4.981749      5.798151      5.616116      0.000000   

       column_cos_5  column_cos_6  
0          4.877077      5.752463  
1          4.877077      5.752463  
2          4.877077      5.752463  
3          4.877077      5.752463  
4          4.877077      5.752463  
...             ...           ...  
24763      4.114313      0.000000  
24764      4.114313      0.000000  
24765      0.000000      0.000000  
24766      0.000000      0.000000  
24767      0.000000      0.000000  

[22515 rows x 7 columns]

In [321]:
sawal = pd.DataFrame()
for i in range(24821):
    print(i)
    if len(data.loc[i,'sent_emb']) < 8:
        sawal.loc[i, "column_cos_22"] = np.linalg.norm(data.loc[i,'quest_emb'][0])

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089


3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3752
3753
3754
3755
3756
3757
3758
3759
3760
3761
3762


5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341
5342
5343
5344
5345
5346
5347
5348
5349
5350
5351
5352
5353
5354
5355
5356
5357
5358
5359
5360
5361
5362
5363
5364
5365
5366
5367
5368
5369
5370
5371
5372
5373
5374
5375
5376
5377
5378
5379
5380
5381
5382
5383
5384
5385
5386
5387
5388
5389
5390
5391
5392
5393
5394
5395
5396
5397
5398
5399
5400
5401
5402
5403
5404
5405
5406
5407
5408
5409
5410
5411
5412
5413
5414


6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978
6979
6980
6981
6982
6983
6984
6985
6986
6987
6988
6989
6990
6991
6992
6993
6994
6995
6996
6997
6998
6999
7000
7001
7002
7003
7004
7005
7006
7007
7008
7009
7010
7011
7012
7013
7014
7015
7016
7017
7018
7019
7020
7021
7022
7023
7024
7025
7026
7027
7028
7029
7030
7031
7032
7033
7034
7035
7036
7037
7038
7039
7040
7041
7042
7043
7044
7045
7046
7047
7048
7049
7050
7051
7052
7053
7054
7055
7056
7057
7058
7059
7060
7061
7062
7063
7064
7065
7066
7067
7068
7069
7070
7071
7072
7073


...

19878
19879
19880
19881
19882
19883
19884
19885
19886
19887
19888
19889
19890
19891
19892
19893
19894
19895
19896
19897
19898
19899
19900
19901
19902
19903
19904
19905
19906
19907
19908
19909
19910
19911
19912
19913
19914
19915
19916
19917
19918
19919
19920
19921
19922
19923
19924
19925
19926
19927
19928
19929
19930
19931
19932
19933
19934
19935
19936
19937
19938
19939
19940
19941
19942
19943
19944
19945
19946
19947
19948
19949
19950
19951
19952
19953
19954
19955
19956
19957
19958
19959
19960
19961
19962
19963
19964
19965
19966
19967
19968
19969
19970
19971
19972
19973
19974
19975
19976
19977
19978
19979
19980
19981
19982
19983
19984
19985
19986
19987
19988
19989
19990
19991
19992
19993
19994
19995
19996
19997
19998
19999
20000
20001
20002
20003
20004
20005
20006
20007
20008
20009
20010
20011
20012
20013
20014
20015
20016
20017
20018
20019
20020
20021
20022
20023
20024
20025
20026
20027
20028
20029
20030
20031
20032
20033
20034
20035
20036
20037
20038
20039
20040
20041
20042
20043
2004

21282
21283
21284
21285
21286
21287
21288
21289
21290
21291
21292
21293
21294
21295
21296
21297
21298
21299
21300
21301
21302
21303
21304
21305
21306
21307
21308
21309
21310
21311
21312
21313
21314
21315
21316
21317
21318
21319
21320
21321
21322
21323
21324
21325
21326
21327
21328
21329
21330
21331
21332
21333
21334
21335
21336
21337
21338
21339
21340
21341
21342
21343
21344
21345
21346
21347
21348
21349
21350
21351
21352
21353
21354
21355
21356
21357
21358
21359
21360
21361
21362
21363
21364
21365
21366
21367
21368
21369
21370
21371
21372
21373
21374
21375
21376
21377
21378
21379
21380
21381
21382
21383
21384
21385
21386
21387
21388
21389
21390
21391
21392
21393
21394
21395
21396
21397
21398
21399
21400
21401
21402
21403
21404
21405
21406
21407
21408
21409
21410
21411
21412
21413
21414
21415
21416
21417
21418
21419
21420
21421
21422
21423
21424
21425
21426
21427
21428
21429
21430
21431
21432
21433
21434
21435
21436
21437
21438
21439
21440
21441
21442
21443
21444
21445
21446
21447
2144

22684
22685
22686
22687
22688
22689
22690
22691
22692
22693
22694
22695
22696
22697
22698
22699
22700
22701
22702
22703
22704
22705
22706
22707
22708
22709
22710
22711
22712
22713
22714
22715
22716
22717
22718
22719
22720
22721
22722
22723
22724
22725
22726
22727
22728
22729
22730
22731
22732
22733
22734
22735
22736
22737
22738
22739
22740
22741
22742
22743
22744
22745
22746
22747
22748
22749
22750
22751
22752
22753
22754
22755
22756
22757
22758
22759
22760
22761
22762
22763
22764
22765
22766
22767
22768
22769
22770
22771
22772
22773
22774
22775
22776
22777
22778
22779
22780
22781
22782
22783
22784
22785
22786
22787
22788
22789
22790
22791
22792
22793
22794
22795
22796
22797
22798
22799
22800
22801
22802
22803
22804
22805
22806
22807
22808
22809
22810
22811
22812
22813
22814
22815
22816
22817
22818
22819
22820
22821
22822
22823
22824
22825
22826
22827
22828
22829
22830
22831
22832
22833
22834
22835
22836
22837
22838
22839
22840
22841
22842
22843
22844
22845
22846
22847
22848
22849
2285

24065
24066
24067
24068
24069
24070
24071
24072
24073
24074
24075
24076
24077
24078
24079
24080
24081
24082
24083
24084
24085
24086
24087
24088
24089
24090
24091
24092
24093
24094
24095
24096
24097
24098
24099
24100
24101
24102
24103
24104
24105
24106
24107
24108
24109
24110
24111
24112
24113
24114
24115
24116
24117
24118
24119
24120
24121
24122
24123
24124
24125
24126
24127
24128
24129
24130
24131
24132
24133
24134
24135
24136
24137
24138
24139
24140
24141
24142
24143
24144
24145
24146
24147
24148
24149
24150
24151
24152
24153
24154
24155
24156
24157
24158
24159
24160
24161
24162
24163
24164
24165
24166
24167
24168
24169
24170
24171
24172
24173
24174
24175
24176
24177
24178
24179
24180
24181
24182
24183
24184
24185
24186
24187
24188
24189
24190
24191
24192
24193
24194
24195
24196
24197
24198
24199
24200
24201
24202
24203
24204
24205
24206
24207
24208
24209
24210
24211
24212
24213
24214
24215
24216
24217
24218
24219
24220
24221
24222
24223
24224
24225
24226
24227
24228
24229
24230
2423

KeyError: 24768

In [322]:
sawal.fillna(0,inplace=True)
sawal

column_cos_22
0           4.436032
1           4.375012
2           5.028121
3           4.146414
4           4.508694
...              ...
24763       4.590540
24764       4.321702
24765       4.211777
24766       4.355690
24767       4.597887

[22515 rows x 1 columns]

In [316]:
data['text']

0                     Saint Bernadette Soubirous
1                      a copper statue of Christ
2                              the Main Building
3        a Marian place of prayer and reflection
4             a golden statue of the Virgin Mary
                          ...                   
24763                         seal and signature
24764                            zakat and khums
24765                               living imams
24766                          Isma'il ibn Jafar
24767                            Ja'far al-Sadiq
Name: text, Length: 24768, dtype: object

In [449]:
jawab = pd.DataFrame()
for i in range(24768):
    if len(data.loc[i,'sent_emb']) < 8:
        x = data.loc[i,'target']
        jawab.loc[i,'column'] = x

In [450]:
jawab

column
0         5.0
1         2.0
2         3.0
3         4.0
4         1.0
...       ...
24763     4.0
24764     5.0
24765     0.0
24766     1.0
24767     1.0

[22515 rows x 1 columns]

In [451]:
from sklearn.model_selection import train_test_split

In [501]:
context_train, context_test, sawal_train, sawal_test, jawab_train, jawab_test = train_test_split(context,sawal,jawab, random_state=40, test_size=0.2)

In [486]:
context_train['column_cos_7'] = sawal_train['column_cos_22']

In [487]:
context_test['column_cos_7'] = sawal_test['column_cos_22']

In [502]:
context_train.shape, context_test.shape , sawal_train.shape , jawab_train.shape

((18012, 7), (4503, 7), (18012, 1), (18012, 1))

In [456]:
from sklearn.ensemble import RandomForestClassifier

In [457]:
forest = RandomForestClassifier()
forest.fit(context_train,jawab_train)

RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [458]:
prediction = forest.predict(context_test)

In [459]:
from sklearn.metrics import classification_report

In [462]:
print(classification_report(jawab_test,prediction,labels=[0,1,2,3,4,5,6]))

              precision    recall  f1-score   support

           0       0.51      0.53      0.52      1683
           1       0.37      0.36      0.36      1169
           2       0.28      0.27      0.28       816
           3       0.24      0.23      0.23       439
           4       0.17      0.17      0.17       240
           5       0.15      0.15      0.15       110
           6       0.27      0.33      0.29        46

    accuracy                           0.38      4503
   macro avg       0.28      0.29      0.29      4503
weighted avg       0.38      0.38      0.38      4503



In [463]:
from sklearn.ensemble import GradientBoostingClassifier

In [464]:
xgb = GradientBoostingClassifier()
xgb.fit(context_train,jawab_train)

GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                           learning_rate=0.1, loss='deviance', max_depth=3,
                           max_features=None, max_leaf_nodes=None,
                           min_impurity_decrease=0.0, min_impurity_split=None,
                           min_samples_leaf=1, min_samples_split=2,
                           min_weight_fraction_leaf=0.0, n_estimators=100,
                           n_iter_no_change=None, presort='deprecated',
                           random_state=None, subsample=1.0, tol=0.0001,
                           validation_fraction=0.1, verbose=0,
                           warm_start=False)

In [465]:
prediction = xgb.predict(context_test)

In [466]:
print(classification_report(jawab_test,prediction,labels=[0,1,2,3,4,5,6]))

              precision    recall  f1-score   support

           0       0.47      0.66      0.55      1683
           1       0.39      0.32      0.35      1169
           2       0.33      0.24      0.27       816
           3       0.29      0.19      0.23       439
           4       0.21      0.13      0.16       240
           5       0.22      0.11      0.15       110
           6       0.21      0.35      0.26        46

    accuracy                           0.41      4503
   macro avg       0.30      0.28      0.28      4503
weighted avg       0.38      0.41      0.38      4503



In [423]:
data.head()

context  \
0  Architecturally, the school has a Catholic cha...   
1  Architecturally, the school has a Catholic cha...   
2  Architecturally, the school has a Catholic cha...   
3  Architecturally, the school has a Catholic cha...   
4  Architecturally, the school has a Catholic cha...   

                                            question  answer_start  \
0  To whom did the Virgin Mary allegedly appear i...           515   
1  What is in front of the Notre Dame Main Building?           188   
2  The Basilica of the Sacred heart at Notre Dame...           279   
3                  What is the Grotto at Notre Dame?           381   
4  What sits on top of the Main Building at Notre...            92   

                                      text  \
0               Saint Bernadette Soubirous   
1                a copper statue of Christ   
2                        the Main Building   
3  a Marian place of prayer and reflection   
4       a golden statue of the Virgin Mary   

                                           sentences  target  \
0  [Architecturally, the school has a Catholic ch...       5   
1  [Architecturally, the school has a Catholic ch...       2   
2  [Architecturally, the school has a Catholic ch...       3   
3  [Architecturally, the school has a Catholic ch...       4   
4  [Architecturally, the school has a Catholic ch...       1   

                                            sent_emb  \
0  [[0.086897895, 0.026372066, 0.015878633, 0.083...   
1  [[0.086897895, 0.026372066, 0.015878633, 0.083...   
2  [[0.086897895, 0.026372066, 0.015878633, 0.083...   
3  [[0.086897895, 0.026372066, 0.015878633, 0.083...   
4  [[0.086897895, 0.026372066, 0.015878633, 0.083...   

                                           quest_emb  
0  [[0.101557314, 0.13133855, 0.04750498, 0.09257...  
1  [[0.097178705, 0.081033505, -0.0014917753, 0.0...  
2  [[0.105155736, 0.07426725, 0.024336234, 0.1249...  
3  [[0.04641258, 0.111463055, -0.048099466, 0.077...  
4  [[0.10152459, 0.10376334, 0.085528575, 0.06222...

In [504]:
question_input = Input(shape=(1,), dtype='int32', name='question_input')
context_input =  Input(shape=(7,), dtype='int32', name='context_input')

questionEmbd = Embedding(output_dim=100, input_dim=20000,
                         mask_zero=False, 
                         input_length=1, trainable=False)(question_input)


contextEmb = Embedding(output_dim=100, input_dim=20000,
                         mask_zero=False,
                         input_length=7, trainable=False)(context_input)

In [505]:
Q = Bidirectional(LSTM(32,return_sequences=True))(questionEmbd)
D = Bidirectional(LSTM(64,return_sequences=True))(contextEmb)
Q_flatten = Flatten()(Q)
D_flatten = Flatten()(D)
merged = concatenate([D_flatten, Q_flatten])

In [506]:
output1 = Dense(1,activation='sigmoid')(merged)

model = Model(inputs=[question_input,context_input], output = output1)
model.compile(optimizer='sgd', loss='mse', metrics=['accuracy'])
model.summary()

Model: "model_26"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
context_input (InputLayer)      (None, 7)            0                                            
__________________________________________________________________________________________________
question_input (InputLayer)     (None, 1)            0                                            
__________________________________________________________________________________________________
embedding_70 (Embedding)        (None, 7, 100)       2000000     context_input[0][0]              
__________________________________________________________________________________________________
embedding_69 (Embedding)        (None, 1, 100)       2000000     question_input[0][0]             
___________________________________________________________________________________________

In [ ]:
model.fit([sawal_train,context_train],jawab_train,epochs=100,batch_size=32)

Epoch 1/100
18012/18012 [==============================] - 16s 901us/step - loss: 2.2223 - accuracy: 0.2710
Epoch 2/100
18012/18012 [==============================] - 11s 603us/step - loss: 2.0789 - accuracy: 0.2707
Epoch 3/100
18012/18012 [==============================] - 11s 609us/step - loss: 2.0699 - accuracy: 0.2707
Epoch 4/100
 2816/18012 [===>..........................] - ETA: 9s - loss: 2.0604 - accuracy: 0.2702